# BocianyiMy

Dane pobierane są z plików .csv w folderze [data](data)

In [6]:
import numpy as np
import pandas as pd
import geopandas as gpd
from geopandas import GeoDataFrame
from datetime import datetime, timedelta
import movingpandas as mpd
import glob

import warnings
warnings.simplefilter("ignore")

import corine_service as cs

import hvplot.pandas # seems to be necessary for the following import to work
from holoviews import opts, renderer
opts.defaults(opts.Overlay(active_tools=['wheel_zoom']))

In [7]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

## Import danych z pliku

Dane pobierane są z plików .csv w folderze ze zmiennej `data_directory_path`.

In [30]:
data_directory_path = r'data'

all_files = glob.glob(data_directory_path + "/De*.csv")

li = []

for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0,sep=None)
    li.append(df)

df = pd.concat(li, axis=0, ignore_index=True)

In [17]:
filename=r'data\Device 6188_jesien_2021.csv'
df = pd.read_csv(filename, index_col=None, header=0,sep=',')

In [31]:
df.columns.values

array(['S/N', 'UUID', 'Transmitting time', 'Collecting time', 'Longitude',
       'Latitude', 'Altitude', 'Geoid height', 'Speed', 'Course',
       'Satellite used', 'Positioning mode', 'GPS time consumption',
       'HorAccuracy', 'VerAccuracy', 'HDOP', 'VDOP', 'Data source'],
      dtype=object)

Wśród danych znajdują się punkty, dla których lokalizacja nie została odczytana (satcount = 0, Longitude = 0, Latitude = 0). W dalszej analizie te punkty zostaną pominięte.

In [14]:
# Ornitella
df = df[(df.satcount != 0)]
df['t'] = pd.to_datetime(df['UTC_datetime'], format='%d.%m.%Y %H:%M')
df = df.drop(columns=['datatype', 'UTC_datetime', 'UTC_time', 'UTC_date', 'satcount', 'U_bat_mV', 'bat_soc_pct', 'solar_I_mA', 'hdop', 'mag_x',	'mag_y', 'mag_z', 'acc_x','acc_y','acc_z'])
df = df.set_index('t').tz_localize(None)
df = df.sort_values(by=['t'])
df = GeoDataFrame(df, geometry=gpd.points_from_xy(df.Longitude, df.Latitude), crs=4326)


AttributeError: 'DataFrame' object has no attribute 'satcount'

In [18]:
# Interrex
df = df[(df.HDOP != 0)]


if "UTC_datetime" in df.columns:
    df["t"] = pd.to_datetime(df["UTC_datetime"], format="%d.%m.%Y %H:%M")
if "Collecting time" in df.columns:
    df['t'] = pd.to_datetime(df['Collecting time'])
if "GPSTime" in df.columns:
    df['t'] = pd.to_datetime(df['GPSTime'], format="%d.%m.%Y %H:%M")
    
#df = df.drop(columns=['datatype', 'UTC_datetime', 'UTC_time', 'UTC_date', 'satcount', 'U_bat_mV', 'bat_soc_pct', 'solar_I_mA', 'hdop', 'mag_x',	'mag_y', 'mag_z', 'acc_x','acc_y','acc_z'])
df = df.set_index('t').tz_localize(None)
df = df.sort_values(by=['t'])
df = GeoDataFrame(df, geometry=gpd.points_from_xy(df.Longitude, df.Latitude), crs=4326)


## Podgląd danych

In [32]:
df

S/N          UUID         Transmitting time       Collecting time  \
0    6188  db0bbc637a3a  2021-08-08T00:06:01.309Z  2021-08-01T08:06:53Z   
1    6188  db0bbc637a3a  2021-08-08T00:06:01.309Z  2021-08-01T12:06:54Z   
2    6188  db0bbc637a3a  2021-08-08T00:06:01.309Z  2021-08-01T16:06:53Z   
3    6188  db0bbc637a3a  2021-08-08T00:06:01.309Z  2021-08-02T07:59:12Z   
4    6188  db0bbc637a3a   2021-08-08T00:06:01.31Z  2021-08-03T05:36:31Z   
..    ...           ...                       ...                   ...   
513  6188  db0bbc637a3a  2021-10-27T00:05:22.315Z  2021-10-26T04:05:53Z   
514  6188  db0bbc637a3a  2021-10-27T00:05:22.316Z  2021-10-26T08:05:10Z   
515  6188  db0bbc637a3a  2021-10-27T00:05:22.317Z  2021-10-26T12:05:48Z   
516  6188  db0bbc637a3a  2021-10-27T00:05:22.317Z  2021-10-26T16:05:00Z   
517  6188  db0bbc637a3a  2021-10-27T00:05:22.318Z  2021-10-26T20:04:55Z   

      Longitude    Latitude  Altitude  Geoid height  Speed  Course  \
0    200.000000  200.000000      0.00          0.00    0.0     0.0   
1    200.000000  200.000000      0.00          0.00    0.0     0.0   
2    200.000000  200.000000      0.00          0.00    0.0     0.0   
3    200.000000  200.000000      0.00          0.00    0.0     0.0   
4     18.784547   52.168851    113.82        153.60    0.1   214.1   
..          ...         ...       ...           ...    ...     ...   
513   12.811497   37.784538   -148.10       -104.78    0.2    48.9   
514   12.808796   37.789597     59.87        103.20    0.3   267.4   
515   12.854026   37.813869     87.24        130.56    1.6     5.1   
516   12.846141   37.820880    260.90        304.24    0.1   176.4   
517   12.846210   37.821046    238.04        281.38    0.2     0.0   

     Satellite used  Positioning mode  GPS time consumption  HorAccuracy  \
0                 0                 0                   150            0   
1                 0                 0                   151            0   
2                 0                 0                   150            0   
3                 0                 0                   150            0   
4                 6                 2                    33            0   
..              ...               ...                   ...          ...   
513               4                 2                    91            0   
514               6                 2                    50            0   
515               4                 2                    90            0   
516               5                 2                    38            0   
517               4                 2                    36            0   

     VerAccuracy  HDOP  VDOP  Data source  
0              0  0.00  0.00            1  
1              0  0.00  0.00            1  
2              0  0.00  0.00            1  
3              0  0.00  0.00            1  
4              0  1.17  0.87            1  
..           ...   ...   ...          ...  
513            0  3.48  1.00            1  
514            0  1.42  0.86            1  
515            0  8.05  0.99            1  
516            0  1.39  0.90            1  
517            0  1.74  0.96            1  

[518 rows x 18 columns]

In [15]:
df.device_id.unique()

AttributeError: 'GeoDataFrame' object has no attribute 'device_id'

In [14]:
df.hvplot.points(tiles="OSM", width=300, height=300, geo=True)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Longitude,Latitude]

In [9]:
df['device_id'].resample('1d').count().hvplot(title='Liczba odczytów na dzień')

:Curve   [t]   (device_id)

In [10]:
t = df.reset_index().t
df = df.assign(delta_t=t.diff().values)
df['delta_t'] = df['delta_t'].dt.total_seconds()/60
pd.DataFrame(df).hvplot.hist('delta_t', title='Histogram interwałów pomiędzy odczytami (w minutach)', bins=130, bin_range=(0, 130))

:Histogram   [delta_t]   (delta_t_count)

Odczyty były wykonywane w seriach z 30 minutowymi odstępami.

## Analiza trajektorii

In [11]:
tc = mpd.TrajectoryCollection(df, 'device_id', t='t')

In [12]:
tc.get_trajectory(171040)

Trajectory 171040 (2019-08-01 03:10:00 to 2020-09-27 15:54:00) | Size: 8808 | Length: 27592948.5m
Bounds: (18.396439, 8.814478, 37.45813, 50.572975)
LINESTRING (20.656475 50.267052, 20.655767 50.268543, 20.655853 50.268543, 20.656084 50.268501, 20.6

In [13]:
traj = tc.trajectories[0]
traj.hvplot(geo=True)

:Overlay
   .Tiles.I :Tiles   [x,y]
   .Path.I  :Path   [Longitude,Latitude]

In [14]:
traj.add_speed()

In [15]:
traj.df.assign(speed=traj.df.speed*3600/1000).hvplot.hist('speed',title="Odcinkowa prędkość [km/h]", bins=100, bin_range=(6,106))

:Histogram   [speed]   (speed_count)

Prędkość obliczona na podstawie różnicy czasu i odległości między punktami.

In [16]:
traj.df.hvplot.hist('speed_km_h',title="Punktowa prędkość [km/h]", bins=100, bin_range=(6,106))

:Histogram   [speed_km_h]   (speed_km_h_count)

Chwilowa prędkość odczytana z nadajnika.

## Porównanie lat

In [17]:
yearly = mpd.TemporalSplitter(tc).split(mode='year')
# monthly = mpd.TemporalSplitter(tc).split(mode='month')

In [18]:
a = yearly.trajectories[0].hvplot(title=yearly.trajectories[0].id, c='speed', line_width=2, cmap='RdYlBu', width=500, height=500, hover_cols=['t'])
for i in range(1, len(yearly)):
    a = a + yearly.trajectories[i].hvplot(title=yearly.trajectories[i].id, c='speed', line_width=2, cmap='RdYlBu', width=500, height=500)
a

:Layout
   .Overlay.I  :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed,t)
   .Overlay.II :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (speed)

## Miejsca postoju

Punkty są zaznaczane na podstawie zmiennych `MAX_DIAMETER` i `MIN_DURATION`. Dla wyznaczonych punktów pobierany jest czas przebywania w tym punkcie i typ pokrycia terenu z mapy [CORINE](https://land.copernicus.eu/pan-european/corine-land-cover/clc2018)

In [19]:
MAX_DIAMETER = 10000 # [m]
MIN_DURATION = timedelta(hours=48)
from geoanalysis import detect_stops

In [30]:
stops = detect_stops(tc, min_duration_h=48, max_diameter=MAX_DIAMETER, include_corine=True)
stops

geometry          start_time  \
stop_id                                                                     
171040_2019-08-01 03:10:00  POINT (20.65648 50.26705) 2019-08-01 03:10:00   
171040_2019-08-12 15:25:00  POINT (21.52441 49.21679) 2019-08-12 15:25:00   
171040_2019-08-15 11:30:00  POINT (22.32626 48.14212) 2019-08-15 11:30:00   
171040_2019-08-20 12:35:00  POINT (22.32879 48.00934) 2019-08-20 12:35:00   
171040_2019-08-23 14:10:00  POINT (22.55893 47.95978) 2019-08-23 14:10:00   
171040_2019-09-07 12:29:00  POINT (22.66130 48.10518) 2019-09-07 12:29:00   
171040_2019-09-20 09:03:00  POINT (26.04288 43.91919) 2019-09-20 09:03:00   
171040_2019-10-11 12:04:00  POINT (19.75597 11.77971) 2019-10-11 12:04:00   
171040_2019-10-14 10:03:00  POINT (19.78521 11.77850) 2019-10-14 10:03:00   
171040_2019-11-07 16:12:00  POINT (19.74992 11.78331) 2019-11-07 16:12:00   
171040_2019-11-10 13:39:00  POINT (19.78661 11.78860) 2019-11-10 13:39:00   
171040_2019-11-14 05:40:00  POINT (19.84465 11.60617) 2019-11-14 05:40:00   
171040_2019-11-16 09:41:00  POINT (19.80133 11.77640) 2019-11-16 09:41:00   
171040_2019-11-19 12:42:00  POINT (19.75281 11.78813) 2019-11-19 12:42:00   
171040_2019-11-26 12:46:00  POINT (19.83520 11.81922) 2019-11-26 12:46:00   
171040_2019-11-29 12:47:00  POINT (19.78013 11.77911) 2019-11-29 12:47:00   
171040_2019-12-17 10:56:00  POINT (19.82405 11.86256) 2019-12-17 10:56:00   
171040_2019-12-27 13:01:00  POINT (19.78805 11.01408) 2019-12-27 13:01:00   
171040_2020-01-01 14:04:00  POINT (19.73961 10.89219) 2020-01-01 14:04:00   
171040_2020-01-12 10:00:00  POINT (21.71738 11.20615) 2020-01-12 10:00:00   
171040_2020-01-23 10:52:00   POINT (22.93086 9.07395) 2020-01-23 10:52:00   
171040_2020-01-26 10:53:00   POINT (23.05515 9.09295) 2020-01-26 10:53:00   
171040_2020-01-30 12:52:00   POINT (22.93907 8.95980) 2020-01-30 12:52:00   
171040_2020-02-05 15:52:00   POINT (22.97273 9.11476) 2020-02-05 15:52:00   
171040_2020-02-10 10:52:00   POINT (22.93725 8.95840) 2020-02-10 10:52:00   
171040_2020-02-16 11:50:00   POINT (22.97748 8.96511) 2020-02-16 11:50:00   
171040_2020-02-23 12:48:00   POINT (22.92190 8.99689) 2020-02-23 12:48:00   
171040_2020-03-04 12:43:00   POINT (22.97752 9.10398) 2020-03-04 12:43:00   
171040_2020-03-08 08:42:00   POINT (23.00748 8.99845) 2020-03-08 08:42:00   
171040_2020-03-14 04:39:00   POINT (22.94159 8.99073) 2020-03-14 04:39:00   
171040_2020-03-21 08:36:00   POINT (22.89977 9.03379) 2020-03-21 08:36:00   
171040_2020-03-23 13:35:00   POINT (22.90202 9.03333) 2020-03-23 13:35:00   
171040_2020-03-26 10:32:00   POINT (22.91359 9.02798) 2020-03-26 10:32:00   
171040_2020-04-28 09:01:00  POINT (31.94791 39.74923) 2020-04-28 09:01:00   
171040_2020-05-10 10:51:00  POINT (31.94842 39.67826) 2020-05-10 10:51:00   
171040_2020-05-20 14:14:00  POINT (30.05732 40.44687) 2020-05-20 14:14:00   
171040_2020-06-02 08:52:00  POINT (20.74916 46.92940) 2020-06-02 08:52:00   
171040_2020-06-08 14:18:00  POINT (21.25838 48.05657) 2020-06-08 14:18:00   
171040_2020-06-14 04:10:00  POINT (21.33612 48.03371) 2020-06-14 04:10:00   
171040_2020-06-20 13:40:00  POINT (21.42913 48.17530) 2020-06-20 13:40:00   
171040_2020-06-28 08:32:00  POINT (21.36735 48.22810) 2020-06-28 08:32:00   
171040_2020-06-30 11:13:00  POINT (21.45005 48.17529) 2020-06-30 11:13:00   
171040_2020-07-05 08:46:00  POINT (21.38641 48.18603) 2020-07-05 08:46:00   
171040_2020-07-11 17:22:00  POINT (21.36890 48.17144) 2020-07-11 17:22:00   
171040_2020-07-20 09:30:00  POINT (21.27631 48.06791) 2020-07-20 09:30:00   
171040_2020-07-31 11:49:00  POINT (20.78077 46.94104) 2020-07-31 11:49:00   
171040_2020-08-05 11:53:00  POINT (21.40995 48.16501) 2020-08-05 11:53:00   
171040_2020-08-08 11:24:00  POINT (20.98131 47.75545) 2020-08-08 11:24:00   
171040_2020-08-11 11:30:00  POINT (20.99048 47.75904) 2020-08-11 11:30:00   
171040_2020-08-18 16:19:00  POINT (20.97977 47.72255) 2020-08-18 16:19:00   
171040_2020-08-28 12:55:00  POINT (20.340

In [21]:
r = renderer('bokeh')
mapa = r.get_plot(stops.hvplot(geo=True, tiles='OSM', color='deeppink', size="duration_h", alpha=0.2, width=500, height=500, hover_cols=['start_time', 'duration_h'])).state
from bokeh.io import output_file, save, show
html = save(mapa, 'graph.html')

In [29]:
 yearly.trajectories[0].hvplot(geo=True, tiles='OSM', line_width=2, width=500, height=500, hover_cols=['t']) + stops.hvplot(geo=True, tiles='OSM', color='deeppink', size="duration_h", alpha=0.2, width=500, height=500, hover_cols=['start_time', 'duration_h'])

:Layout
   .Overlay.I  :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (t)
   .Overlay.II :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]   (duration_h,start_time)

## Wykresy

In [23]:
pd.DataFrame(stops).hvplot.bar(title='Długość postoju (w godzinach) w zależności od godziny i miesiąca', 
                                     x='start_time.month', y=['duration_h'], stacked=True)

:Bars   [start_time.month,Variable]   (value)

In [24]:
pd.DataFrame(traj.df).hvplot.heatmap(title='Średnia prędkość [m/s] w zależności od godziny i miesiąca', 
                                     x='t.hour', y='t.month', C='speed', reduce_function=np.mean)

:HeatMap   [t.hour,t.month]   (speed)

In [25]:
pd.DataFrame(traj.df).hvplot.heatmap(title='Średnia temperatura w zależności od godziny i miesiąca', 
                                     x='t.hour', y='t.month', C='temperature_C', reduce_function=np.mean)

:HeatMap   [t.hour,t.month]   (temperature_C)